In [1]:
# 필요한 라이브러리만 임포트
import numpy as np  # 다차원 배열을 다루기 위한 라이브러리
import librosa  # 음악 및 오디오 분석을 위한 라이브러리
import os  # 운영 체제와 상호 작용하기 위한 라이브러리, 파일 경로 조작 등
import tensorflow as tf  # 머신러닝 및 신경망을 위한 라이브러리
import pandas as pd  # 데이터 분석 및 조작을 위한 라이브러리
from IPython.display import clear_output  # Jupyter 노트북의 출력을 지우기 위한 함수
import matplotlib.pyplot as plt  # 데이터 시각화를 위한 라이브러리

# Jupyter 노트북에서 matplotlib의 그래프를 인라인으로 표시하도록 설정
%matplotlib inline  

import seaborn as sns  # matplotlib 기반의 고급 시각화 라이브러리
import torch  # 딥러닝 프레임워크 중 하나
from sklearn.model_selection import train_test_split  # 데이터를 훈련 세트와 테스트 세트로 분할하기 위한 함수
from sklearn.metrics import accuracy_score, precision_score, recall_score  # 모델 평가를 위한 성능 지표 계산 함수
from tensorflow.keras import layers, losses  # TensorFlow의 케라스 API를 사용하여 신경망의 층과 손실 함수를 정의
from tensorflow.keras.models import Model  # TensorFlow의 케라스 API를 사용하여 모델을 정의 및 관리
from tensorflow.python.ops.numpy_ops import np_config  # TensorFlow에서 numpy와의 호환성을 위한 설정
np_config.enable_numpy_behavior()  # TensorFlow에서 numpy와 유사한 동작을 활성화

# 사용자 정의 유틸리티 함수 임포트
from util import play_audio, load_audio, get_features, get_mfcc, get_lmfe, get_chroma, plot_chroma, plot_mfcc, plot_lmfe
# 오디오 데이터를 다루기 위한 사용자 정의 함수들 (재생, 로드, 특징 추출 등)

# Seaborn 스타일 설정
sns.set(style="white", palette="muted")  # Seaborn 그래프의 기본 스타일 설정
sns.set_style("ticks", {"xtick.major.size": 8, "ytick.major.size": 8})  # Seaborn 그래프의 세부 스타일 설정

2024-06-18 09:57:00.161615: I tensorflow/core/util/util.cc:169] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-06-18 09:57:00.239426: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2024-06-18 09:57:00.239445: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


In [234]:
# MIMII 데이터 형식 : "data/MIMII/{db에 따른 데이터 경로}/{기계 종류}/{기계 ID}/{normal or abnormal}/{파일 이름}"
# DCASE 데이터 형식 : "data/DCASE/{year}/{dataset_class}/{machine_type}/{data_class}/{file_name}"

base_dir = "data/"  # 데이터셋이 저장된 디렉토리 경로

data_case = [ "DCASE", "MIMII" ] # 분류할 데이터셋의 종류

dcase_years = [ "2020", "2021", "2022", "2023", "2024" ]  # 분류할 데이터셋의 연도

# DCASE 데이터셋의 경우, 2020년부터 2024년까지의 데이터셋이 있으며, 2023년과 2024년의 데이터셋은 개발용 데이터셋만 존재
dcase_year_contains_all = [ # 분류할 데이터셋의 연도 (전체)
    "2020", 
    "2021", 
    "2022",
    # "2023",
    # "2024",
] 

dcase_year_contains_only_dev = [ # 분류할 데이터셋의 연도 (개발용 데이터만 있는 연도)
    "2023",
    "2024",
]

dcase_dev_eval_additional = [ # 분류할 데이터셋의 종류
    "dev",
    "eval",
    "add",
]

dcase_data_class = [ "train", "test" ]  # 분류할 데이터셋의 종류

# MIMII 데이터셋의 경우, -6dB, 0dB, 6dB의 데이터가 있음
mimii_dbs = [ # db에 따른 데이터 경로
    "data_-6_db",
    "data_0_db",
    "data_6_db",
]

mimii_ids = [
    "id_00",
    "id_02",
    "id_04",
    "id_06",
]

machine_types = [ "fan", "valve" ]  # 분류할 기계의 종류
data_class = [ "normal", "abnormal", "unknown"]  # 분류할 데이터의 종류

In [235]:
def get_data_paths_and_labels(machine, base_dir="data/") : 
    '''
    Before find data, get datasets names and labels in specific machine
    dirs[”DCASE”][”2020”][”dev”]["train"][”normal”] = {real_path}
    dirs[”MIMII”][”data_-6_db”]["id_00][”normal”] = {real_path}

    inputs :
    machine : 기기 이름
    base_dir : 데이터가 저장된 기본 경로

    outputs :
    dirs : dictionary of dataset names
    labels : dictionary of dataset labels (0 is abnormal, 1 is normal, -1 is something wrong)
    '''

    data_dict = dict()
    label_dict = dict()
    
    # TODO : other iterations for each data_case

    # DCASE
    # data_dict[data_case[0]] = dict()
    # label_dict[data_case[0]] = dict()

    # for year in dcase_years :
    #     data_dict[data_case[0]][year] = dict()
    #     label_dict[data_case[0]][year] = dict()
        
    #     data_dict[data_case[0]][year], label_dict[data_case[0]][year] = get_from_dcase(machine, year, base_dir = base_dir)
    
    # MIMII
    data_dict[data_case[1]] = dict()
    label_dict[data_case[1]] = dict()

    for decibel in mimii_dbs :
        data_dict[data_case[1]][decibel] = dict()
        label_dict[data_case[1]][decibel] = dict()

        data_dict[data_case[1]][decibel], label_dict[data_case[1]][decibel] = get_from_mimii(machine, decibel, base_dir = base_dir)

    return data_dict, label_dict


def get_from_dcase(machine, year, base_dir) :
    '''
    data_path를 조합 -> get_dcase_data_paths_and_labels_from_edge_dir 함수에 넣어서 데이터셋의 디렉토리 경로와 label을 추출
    data_path key : 
    data_path value : "data/DCASE/{year}/{dataset_class}/{machine_type}/{data_class}/{file_name}"
    inputs
    year : string, 데이터셋의 연도
    base_dir : string, 데이터셋이 저장된 디렉토리 경로

    outputs
    data_dict : dictionary, 데이터셋의 디렉토리 경로, { key : dataset_class, value : data_path}
    labels : dictionary, 데이터셋의 label { key : data_path, value : label_list}
    '''

    data_dict = dict()
    label_dict = dict()
    for dataset_class in dcase_dev_eval_additional : 

        if year in dcase_year_contains_only_dev and dataset_class != dcase_dev_eval_additional[0] :
            continue

        data_path = base_dir + "DCASE/" + year + "/" # data/DCASE/2020/
        data_path = data_path + dataset_class + "/" + machine + "/" # data/DCASE/2020/dev/fan/

        data_dict[dataset_class] = dict()
        label_dict[dataset_class] = dict()

        for each_data_class in dcase_data_class :
            tmp_data_path = data_path + each_data_class + "/" # tmp_data_path : "data/DCASE/2020/dev/fan/train/"
            
            if dataset_class == dcase_dev_eval_additional[1] and each_data_class == dcase_data_class[0] :
                continue
            if dataset_class == dcase_dev_eval_additional[2] and each_data_class == dcase_data_class[1] :
                continue
            
            data_dict[dataset_class][each_data_class] = dict()
            label_dict[dataset_class][each_data_class] = dict()

            data_dict[dataset_class][each_data_class], label_dict[dataset_class][each_data_class] = get_data_paths_and_labels_from_edge_dir(tmp_data_path)

    return data_dict, label_dict
        

def get_from_mimii(machine, decibel, base_dir) :

    data_dict = dict()
    label_dict = dict()
    for decibel in mimii_dbs :
        data_path = base_dir + "MIMII/" + decibel + "/" + machine + '/' # data/MIMII/data_-6_dB/fan/
        
        data_dict[decibel] = dict()
        label_dict[decibel] = dict()
        for each_id in mimii_ids :
            data_path = data_path + each_id + "/" # data/MIMII/data_-6_dB/fan/id_00/

            for each_data_class in data_class :
                if each_data_class == data_class[2] :
                    break
                tmp_data_path = data_path + each_data_class + "/" # tmp_data_path : "data/MIMII/data_-6_dB/fan/id_00/normal/"

                data_dict[decibel], label_dict[decibel] = get_data_paths_and_labels_from_edge_dir(tmp_data_path)

    return data_dict, label_dict
        
def get_data_paths_and_labels_from_edge_dir(data_path) :
    '''
    data_path 에 있는 모든 *.wav 파일의 경로와 label을 dircionary로 반환
    label_dict 가 의미 없는 값일 수 있으나, label 값을 binary 로 mapping 하기 위해 사용

    inputs
    data_path : string, *.wav 파일이 저장된 디렉토리 경로

    outputs
    data_dict : dictionary, { key : normal or abnormal, value : 디렉토리에 있는 모든 *.wav 파일의 경로를 저장한 리스트 }
    label_dict : dictionary, { key : 디렉토리에 있는 모든 *.wav 파일의 경로, value : label }
    '''
    
    data_dict = dict()
    label_dict = dict()

    for each_class in data_class :
        data_dict[each_class] = []

    data_path_list = os.listdir(data_path) # data_path에 있는 모든 파일 리스트
    for each_data in data_path_list :
        each_data_full_path = data_path + "/" + each_data # data_path에 있는 각 파일의 전체 경로
        dirname = data_path.split("/")[-2] # data_path의 마지막 디렉토리 이름

        if data_class[0] in each_data or dirname == data_class[0] :
            data_dict[data_class[0]].append(each_data_full_path)
            label_dict[each_data_full_path] = 1
        elif data_class[1] in each_data or "anomal" in each_data or dirname == data_class[1] :
            data_dict[data_class[1]].append(each_data_full_path)
            label_dict[each_data_full_path] = 0
        else : 
            data_dict[data_class[2]].append(each_data_full_path)
            label_dict[each_data_full_path] = -1

    print(data_path.split('/')[1:-1])
    
    return data_dict, label_dict


In [236]:
fan_paths, fan_labels = get_data_paths_and_labels("fan")

['MIMII', 'data_-6_db', 'fan', 'id_00', 'normal']
['MIMII', 'data_-6_db', 'fan', 'id_00', 'abnormal']


FileNotFoundError: [Errno 2] No such file or directory: 'data/MIMII/data_-6_db/fan/id_00/id_02/normal/'

In [207]:
import json
from collections import Counter

def summarize_json(data, indent=0, key_prefix=""):
    """
    JSON 데이터를 요약하여 구조를 출력하는 함수
    """
    if isinstance(data, dict):
        print(' ' * indent + '{')
        for key, value in data.items():
            print(' ' * (indent + 2) + f'"{key}": ', end='')
            summarize_json(value, indent + 2, key_prefix=key_prefix + key + "/")
        print(' ' * indent + '}')
    elif isinstance(data, list):
        print(' ' * indent + '[')
        if data:
            item_types = Counter(type(item).__name__ for item in data)
            for item_type, count in item_types.items():
                print(' ' * (indent + 2) + f'{item_type} x {count}')
            for item in data[:1]:  # First item example
                summarize_json(item, indent + 2, key_prefix=key_prefix)
            if len(data) > 1:
                print(' ' * (indent + 2) + '...')
        print(' ' * indent + ']')
    else:
        print(' ' * indent + f'{type(data).__name__}')


In [208]:
summarize_json(fan_paths["DCASE"])

{
  "2020":   {
    "dev":     {
      "train":       {
        "normal":         [
          str x 3675
          str
          ...
        ]
        "abnormal":         [
        ]
        "unknown":         [
        ]
      }
      "test":       {
        "normal":         [
          str x 400
          str
          ...
        ]
        "abnormal":         [
          str x 1475
          str
          ...
        ]
        "unknown":         [
        ]
      }
    }
    "eval":     {
      "test":       {
        "normal":         [
        ]
        "abnormal":         [
        ]
        "unknown":         [
          str x 1342
          str
          ...
        ]
      }
    }
    "add":     {
      "train":       {
        "normal":         [
          str x 2846
          str
          ...
        ]
        "abnormal":         [
        ]
        "unknown":         [
        ]
      }
    }
  }
  "2021":   {
    "dev":     {
      "train":       {
        "normal":     

In [200]:
summarize_json(fan_labels["DCASE"])

{
  "2020":   {
    "dev":     {
      "train":       {
        "data/DCASE/2020/dev/fan/train//normal_id_00_00000000.wav":         int
        "data/DCASE/2020/dev/fan/train//normal_id_00_00000001.wav":         int
        "data/DCASE/2020/dev/fan/train//normal_id_00_00000002.wav":         int
        "data/DCASE/2020/dev/fan/train//normal_id_00_00000003.wav":         int
        "data/DCASE/2020/dev/fan/train//normal_id_00_00000004.wav":         int
        "data/DCASE/2020/dev/fan/train//normal_id_00_00000005.wav":         int
        "data/DCASE/2020/dev/fan/train//normal_id_00_00000006.wav":         int
        "data/DCASE/2020/dev/fan/train//normal_id_00_00000007.wav":         int
        "data/DCASE/2020/dev/fan/train//normal_id_00_00000008.wav":         int
        "data/DCASE/2020/dev/fan/train//normal_id_00_00000009.wav":         int
        "data/DCASE/2020/dev/fan/train//normal_id_00_00000010.wav":         int
        "data/DCASE/2020/dev/fan/train//normal_id_00_00000011.wa

In [201]:
valve_paths, valve_labels = get_data_paths_and_labels("valve")

In [202]:
summarize_json(valve_paths["DCASE"])

{
  "2020":   {
    "dev":     {
      "train":       {
        "normal":         [
          str x 3291
          str
          ...
        ]
        "abnormal":         [
        ]
        "unknown":         [
        ]
      }
      "test":       {
        "normal":         [
          str x 400
          str
          ...
        ]
        "abnormal":         [
          str x 479
          str
          ...
        ]
        "unknown":         [
        ]
      }
    }
    "eval":     {
      "test":       {
        "normal":         [
        ]
        "abnormal":         [
        ]
        "unknown":         [
          str x 940
          str
          ...
        ]
      }
    }
    "add":     {
      "train":       {
        "normal":         [
          str x 2531
          str
          ...
        ]
        "abnormal":         [
        ]
        "unknown":         [
        ]
      }
    }
  }
  "2021":   {
    "dev":     {
      "train":       {
        "normal":       

In [203]:
summarize_json(valve_labels["DCASE"])

{
  "2020":   {
    "dev":     {
      "train":       {
        "data/DCASE/2020/dev/valve/train//normal_id_00_00000000.wav":         int
        "data/DCASE/2020/dev/valve/train//normal_id_00_00000001.wav":         int
        "data/DCASE/2020/dev/valve/train//normal_id_00_00000002.wav":         int
        "data/DCASE/2020/dev/valve/train//normal_id_00_00000003.wav":         int
        "data/DCASE/2020/dev/valve/train//normal_id_00_00000004.wav":         int
        "data/DCASE/2020/dev/valve/train//normal_id_00_00000005.wav":         int
        "data/DCASE/2020/dev/valve/train//normal_id_00_00000006.wav":         int
        "data/DCASE/2020/dev/valve/train//normal_id_00_00000007.wav":         int
        "data/DCASE/2020/dev/valve/train//normal_id_00_00000008.wav":         int
        "data/DCASE/2020/dev/valve/train//normal_id_00_00000009.wav":         int
        "data/DCASE/2020/dev/valve/train//normal_id_00_00000010.wav":         int
        "data/DCASE/2020/dev/valve/train//